In [ ]:
import numpy as np
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
from tqdm import trange
from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/MyDrive/Colab_Notebooks/Marvel_network

Mounted at /content/drive
/content/drive/MyDrive/Colab_Notebooks/Marvel_network


In [ ]:
# Read datasets
elements=pd.read_csv('source_data/nodes.csv')
hero=elements[elements['type']=='hero']['node']
comic=elements[elements['type']=='comic']['node']
hero_comic=pd.read_csv('source_data/edges.csv')
print(len(hero_comic))
hero_hero=pd.read_csv('source_data/hero-network.csv')
print(len(hero_hero))

96104
574467


In [ ]:
# Create hero and comic lists
hero=list((set(hero_hero['hero1']).union(
    set(hero_hero['hero2']))).intersection(
        set(hero_comic['hero'])).intersection(
            set(hero)
        ))

comic=list(set(hero_comic['comic']).intersection(set(comic)))

# Delete edges containing unknown hero/comic
hero_comic=hero_comic[hero_comic['comic'].isin(comic)]
hero_comic=hero_comic[hero_comic['hero'].isin(hero)]
print(len(hero_comic))

hero_hero=hero_hero[hero_hero['hero1'].isin(hero)]
hero_hero=hero_hero[hero_hero['hero2'].isin(hero)]
print(len(hero_hero))

82593
424270


In [ ]:
# Determine in which comics the hero pairs meet
hero_hero_comic=pd.DataFrame(columns=['hero1','hero2','comic'])
for i in trange(len(hero)):
    hero1=hero[i]
    pair1=hero_comic[hero_comic['hero']==hero1]
    hero_comic=hero_comic[hero_comic['hero']!=hero1]
    pair2=hero_comic[hero_comic['comic'].isin(pair1['comic'])]
    pair2.columns=['hero2', 'comic']
    pair2.insert(0,'hero1',hero1,True)
    hero_hero_comic=pd.concat([hero_hero_comic,pair2])

100%|██████████| 6282/6282 [02:20<00:00, 44.62it/s]


In [ ]:
def flatten_list(matrix):
    flat_list = []
    for row in matrix:
        flat_list += row
    return flat_list

# List unique pairs
existing_pairs=hero_hero_comic[['hero1','hero2']].drop_duplicates()
existing_pairs=[[(existing_pairs.iloc[i]['hero1'],existing_pairs.iloc[i]['hero2']),
                 (existing_pairs.iloc[i]['hero2'],existing_pairs.iloc[i]['hero1']) ]
                 for i in trange(len(existing_pairs))]
existing_pairs=flatten_list(existing_pairs)

hero_hero=hero_hero.groupby(['hero1','hero2']).size().reset_index(name='counts')
adding_pairs=hero_hero.drop_duplicates()
adding_pairs=[(adding_pairs.iloc[i]['hero1'],adding_pairs.iloc[i]['hero2'])
                 for i in trange(len(adding_pairs))
                 if adding_pairs.iloc[i]['hero1']!=adding_pairs.iloc[i]['hero2']]


100%|██████████| 183645/183645 [01:15<00:00, 2442.47it/s]


In [ ]:
# Create a dataframe, containing hero pairs and the comics with them
unknown_pairs=list(set(adding_pairs)-set(existing_pairs))
for pair in unknown_pairs:
    hero1=pair[0]
    hero2=pair[1]
    if len(hero_hero[(hero_hero['hero1']==pair[0]) & (hero_hero['hero2']==pair[1])])==1:
        count=hero_hero[(hero_hero['hero1']==pair[0]) & (hero_hero['hero2']==pair[1])]['counts'].iloc[0]
        for i in range(int(count)):
            hero_hero_comic.loc[len(hero_hero_comic)]=[hero1,hero2,'UNKNOWN']
    else:
        continue

hero_hero_comic=hero_hero_comic.reset_index(drop=True)
hero_hero_comic

hero1                 hero2    comic
0                     ZAKKA          BROTHER TODE      E 1
1                     ZAKKA    DAMIAN, DR. DANIEL      E 1
2                     ZAKKA         DAMIAN, MARGO      E 1
3                     ZAKKA  IKARIS/IKE HARRIS [E      E 1
4                     ZAKKA      KARKAS [DEVIANT]      E 1
...                     ...                   ...      ...
426553          BLAQUESMITH  PSYLOCKE/ELISABETH B    C2 31
426554          BLAQUESMITH  PSYLOCKE/ELISABETH B  X:PRIME
426555  PALADIN/PAUL DENNIS       FROST, ADRIENNE  GENX 52
426556  PALADIN/PAUL DENNIS       FROST, ADRIENNE  GENX 53
426557  PALADIN/PAUL DENNIS       FROST, ADRIENNE  GENX 54

[426558 rows x 3 columns]

In [ ]:
# Create weighted adjacent matrix/list for this network
hero_hero=hero_hero_comic.groupby(['hero1','hero2']).size().reset_index(name='counts')
hero_hero

hero1                 hero2  counts
0       3-D MAN/CHARLES CHAN  AJAK/TECUMOTZIN [ETE       1
1       3-D MAN/CHARLES CHAN  ANGEL/WARREN KENNETH       1
2       3-D MAN/CHARLES CHAN  ANT-MAN II/SCOTT HAR       1
3       3-D MAN/CHARLES CHAN  ANT-MAN/DR. HENRY J.       2
4       3-D MAN/CHARLES CHAN  ARABIAN KNIGHT/ABDUL       1
...                      ...                   ...     ...
142284                 ZZZAX      RODRIGUEZ, DEBRA       1
142285                 ZZZAX  SUMMERS, NATHAN CHRI       1
142286                 ZZZAX         TALBOT, GLENN       1
142287                 ZZZAX    TIGRA/GREER NELSON       1
142288                 ZZZAX  WONDER MAN/SIMON WIL       1

[142289 rows x 3 columns]

In [ ]:
# Create Weighted Adjcent Matrix. weight to be the times the hero pair shows together; values on diagnal to be the degree of each node
G=nx.from_pandas_edgelist(hero_hero,'hero1','hero2',edge_attr='counts')
G=nx.Graph(G)
Adj=nx.adjacency_matrix(G,weight='counts').todense()
deg=[x[1] for x in list(G.degree)]
for i in range(len(Adj)):
    Adj[i,i]=deg[i]
hero=list(G.nodes)
Adj=pd.DataFrame(Adj,columns=hero,index=hero)
Adj

3-D MAN/CHARLES CHAN  AJAK/TECUMOTZIN [ETE  \
3-D MAN/CHARLES CHAN                   102                     1   
AJAK/TECUMOTZIN [ETE                     1                   175   
ANGEL/WARREN KENNETH                     1                     1   
ANT-MAN II/SCOTT HAR                     1                     1   
ANT-MAN/DR. HENRY J.                     2                     0   
...                                    ...                   ...   
YSSA                                     0                     0   
ZAKKA                                    0                     0   
ZCANN                                    0                     0   
ZEAKLAR                                  0                     0   
ZZZAX                                    0                     0   

                      ANGEL/WARREN KENNETH  ANT-MAN II/SCOTT HAR  \
3-D MAN/CHARLES CHAN                     1                     1   
AJAK/TECUMOTZIN [ETE                     1                     1   
ANGEL/WARREN KENNETH                  1083                     3   
ANT-MAN II/SCOTT HAR                     3                   383   
ANT-MAN/DR. HENRY J.                    25                    14   
...                                    ...                   ...   
YSSA                                     0                     0   
ZAKKA                                    0                     0   
ZCANN                                    0                     0   
ZEAKLAR                                  0                     0   
ZZZAX                                    0                     1   

                      ANT-MAN/DR. HENRY J.  ARABIAN KNIGHT/ABDUL  \
3-D MAN/CHARLES CHAN                     2                     1   
AJAK/TECUMOTZIN [ETE                     0                     1   
ANGEL/WARREN KENNETH                    25                     4   
ANT-MAN II/SCOTT HAR                    14                     1   
ANT-MAN/DR. HENRY J.                  1063                     0   
...                                    ...                   ...   
YSSA                                     0                     0   
ZAKKA                                    0                     0   
ZCANN                                    2                     0   
ZEAKLAR                                  0                     0   
ZZZAX                                    1                     0   

                      BANNER, BETTY ROSS T  BEAST/HENRY &HANK& P  \
3-D MAN/CHARLES CHAN                     2                     1   
AJAK/TECUMOTZIN [ETE                     0                     1   
ANGEL/WARREN KENNETH                     2                   305   
ANT-MAN II/SCOTT HAR                     1                     7   
ANT-MAN/DR. HENRY J.                     8                    98   
...                                    ...                   ...   
YSSA                                     0                     0   
ZAKKA                                    0                     0   
ZCANN                                    0                     0   
ZEAKLAR                                  0                     0   
ZZZAX                                    3                     0   

                      BLACK BOLT/BLACKANTO  BLACK PANTHER/T'CHAL  ...  \
3-D MAN/CHARLES CHAN                     1                     1  ...   
AJAK/TECUMOTZIN [ETE                     1                     1  ...   
ANGEL/WARREN KENNETH                     8                    11  ...   
ANT-MAN II/SCOTT HAR                     9                     8  ...   
ANT-MAN/DR. HENRY J.                     7                    86  ...   
...                                    ...                   ...  ...   
YSSA                                     0                     0  ...   
ZAKKA                                    0                     0  ...   
ZCANN                                    0                     1  ...   
ZEAKLAR                 

In [ ]:
# save the tables
hero_hero_comic.to_csv('hero_hero_comic.csv',index=False)
hero_hero.to_csv('adjacency_list.csv',index=False)
Adj.to_csv('adjacency_matrix.csv')
Adj.iloc[:50,:50].to_csv('adjacency_matrix_preview.csv')